In [94]:
import numpy as np
import pandas as pd
import plotly.graph_objects as go
from plotly.offline import download_plotlyjs, init_notebook_mode, plot, iplot

#### Reading the file and sorting based on timestamp

In [95]:
gaze_data = pd.read_csv('gaze_positions.csv')
gaze_data.sort_values(["gaze_timestamp"], 
                    ascending=[True], 
                    inplace=True)


#### Filtering out the calibration sequence

In [110]:
startTime = 10
endTime = 70

plTime_fr = np.array(gaze_data['gaze_timestamp'] - gaze_data['gaze_timestamp'].iloc[0])
startIndex = next(idx for idx, val in enumerate(plTime_fr) if val >  startTime)
endIndex = next(idx for idx, val in enumerate(plTime_fr) if val >  endTime)
plTime_fr = gaze_data[startIndex:endIndex]
plIndex = np.arange(len(plTime_fr))

#### Get 3 point coordinates
This is reusable function to get any 3point coordinates from the file

In [97]:
def get_3d_coordinates(row,coordinates_name):
    return [row['{}_x'.format(coordinates_name)],row['{}_y'.format(coordinates_name)],row['{}_z'.format(coordinates_name)]]

#### Get spherical coordinates
This is a reusable function to convert any cartesan coordinates to spherical coordinates

In [98]:
def get_spherical_coordinates(row,coordinates_name):
    coordinates = get_3d_coordinates(row,coordinates_name)
    az = np.rad2deg(np.arctan(np.divide(coordinates[0],coordinates[2])))
    el = np.rad2deg(np.arctan(np.divide(coordinates[1],coordinates[2])))
    return [az,el]

#### Get gaze point in world camera
This is done by converting the 3d gaze point from cartesan to spherical coordinates and then adding it as a new column in the csv file

In [99]:
azEl = gaze_data.apply(lambda arbitraryRowName: get_spherical_coordinates(arbitraryRowName,'gaze_point_3d'),axis=1)
gaze_data['gazeInWorldCam_az'],gaze_data['gazeInWorldCam_el'] = zip(*azEl)
list(gaze_data)

['gaze_timestamp',
 'world_index',
 'confidence',
 'norm_pos_x',
 'norm_pos_y',
 'base_data',
 'gaze_point_3d_x',
 'gaze_point_3d_y',
 'gaze_point_3d_z',
 'eye_center0_3d_x',
 'eye_center0_3d_y',
 'eye_center0_3d_z',
 'gaze_normal0_x',
 'gaze_normal0_y',
 'gaze_normal0_z',
 'eye_center1_3d_x',
 'eye_center1_3d_y',
 'eye_center1_3d_z',
 'gaze_normal1_x',
 'gaze_normal1_y',
 'gaze_normal1_z',
 'gazeInWorldCam_az',
 'gazeInWorldCam_el']

Plotting Azimuth and elevation

In [109]:

# fig = go.Figure([go.Scatter(x=plIndex, y=gaze_data['gazeInWorldCam_az'])])
# fig.show()
# fig = go.Figure([go.Scatter(x=plIndex, y=gaze_data['gazeInWorldCam_el'])])
# fig.show()

traces = []
az_plot = go.Scatter(x=plIndex, y=gaze_data['gazeInWorldCam_az'], marker_color = 'rgba(37, 99, 235, 1)', marker_size = 2, name = 'Azimuth')
traces.append(az_plot)
el_plot = go.Scatter(x=plIndex, y=gaze_data['gazeInWorldCam_el'], marker_color = 'rgba(44, 198, 237, 1)', marker_size = 2, name = 'Elevation')
traces.append(el_plot)

yLim=[-50,50]
layout = dict(
    dragmode= 'pan',
    yaxis=dict(range=yLim, title='Degree'),
    xaxis=dict(
        rangeslider=dict(visible=True)
    )
)


fig = go.Figure(
    data = traces,
    layout = layout
)
fig.show()

